# Putting it all together 

For this practice we will practice putting different elements on a map and learn how to put them on in a way that they become multiples layers on the leaflet map that can be toggled off and on. 

For this practice, we will explore the following data sets:
 * European Countries Geo Json file, FYI includes part of Israel - located in the data directory for this module (europe.geojson). This will be used to create a Choropleth using population values
 * Points of Interest shape file (http://www.mapcruzin.com/download-shapefile/europe-places-shape.zip ), we will be using the first 100 so as to not overload the system. This will be used to create markers 
 
##### Backup Data File 
 * [europe-places-shape.zip](https://web.dsa.missouri.edu/static/data/geodata/europe-places-shape.zip)

In [1]:
# import packages
import pandas as pd
import geopandas as gpd
import json
import sys
import os
import urllib.request
import shutil
from pathlib import Path
from zipfile import ZipFile
import folium
from folium.plugins import MarkerCluster
from branca.colormap import linear

## Task 1: Load Data
Load the dataset to be used.

In [2]:
## M7:P1:Cell01
# Add Your Code load the European Countries dataset
# -------------------------------------------------
geojson_europe = json.load(open('/dsa/data/geospatial/GeoVis/europe.geojson'))
print(geojson_europe)
europe = gpd.read_file('/dsa/data/geospatial/GeoVis/europe.geojson')
europe.head()

{'type': 'FeatureCollection', 'features': [{'type': 'Feature', 'properties': {'FID': 0.0, 'FIPS': 'AJ', 'ISO2': 'AZ', 'ISO3': 'AZE', 'UN': 31, 'NAME': 'Azerbaijan', 'AREA': 8260, 'POP2005': 8352021, 'REGION': 142, 'SUBREGION': 145, 'LON': 47.395, 'LAT': 40.43}, 'geometry': {'type': 'MultiPolygon', 'coordinates': [[[[45.083321, 39.768044000000145], [45.266388, 39.61110700000012], [45.319984, 39.546944], [45.326096, 39.538322], [45.330826000000116, 39.535271], [45.457497, 39.49360700000011], [45.47248100000013, 39.494431], [45.49694, 39.502213], [45.507767, 39.506653], [45.5283280000001, 39.517212], [45.558327, 39.53387500000014], [45.59054600000013, 39.54861], [45.60777, 39.554703], [45.626656, 39.55999], [45.725266, 39.57972], [45.732201000000146, 39.580544000000145], [45.740822, 39.57972], [45.755272, 39.576653], [45.783333, 39.56915300000014], [45.80054500000011, 39.561928], [45.811371, 39.55637400000012], [45.81998, 39.54972], [45.823044, 39.545273], [45.829987, 39.455544], [45.8299

FID FIPS ISO2 ISO3   UN                    NAME   AREA  POP2005  REGION  \
0  0.0   AJ   AZ  AZE   31              Azerbaijan   8260  8352021     142   
1  0.0   AL   AL  ALB    8                 Albania   2740  3153731     150   
2  0.0   AM   AM  ARM   51                 Armenia   2820  3017661     142   
3  0.0   BK   BA  BIH   70  Bosnia and Herzegovina   5120  3915238     150   
4  0.0   BU   BG  BGR  100                Bulgaria  11063  7744591     150   

   SUBREGION     LON     LAT  \
0        145  47.395  40.430   
1         39  20.068  41.143   
2        145  44.563  40.534   
3         39  17.786  44.169   
4        151  25.231  42.761   

                                            geometry  
0  MULTIPOLYGON (((45.08332 39.76804, 45.26639 39...  
1  POLYGON ((19.43621 41.02107, 19.45055 41.06000...  
2  MULTIPOLYGON (((45.57305 40.63249, 45.52888 40...  
3  POLYGON ((17.64984 42.88908, 17.57853 42.94382...  
4  POLYGON ((27.87917 42.84110, 27.89500 42.80250...

In [3]:
## M7:E1:Cell02
# Add Your Code to Download / unzip and load the intresting places data.
# ----------------------------------------------------------------------
file_URL = 'https://web.dsa.missouri.edu/static/data/geodata/europe-places-shape.zip'

local_file_name = 'europe-places-shape.zip'


file_Path = Path('../data/')  
file_Path /= local_file_name

with urllib.request.urlopen(file_URL) as response,  file_Path.open(mode='w+b') as out_file:
    shutil.copyfileobj(response, out_file)

to_unzip = ZipFile('../data/europe-places-shape.zip', 'r')
unzipped = '../data/europe_interest_places'
to_unzip.extractall(unzipped)
to_unzip.close()
for file in os.listdir(unzipped):
    if file.endswith(".shp"):
        shape_file =  unzipped + '/' + file
        
interest = gpd.read_file('../data/europe_interest_places')
interest.head()

osm_id              name     type  population                   geometry
0       2  Wiesbaden-Naurod  village           0   POINT (8.30130 50.13594)
1  104849           Bristol     city           0  POINT (-2.59539 51.45582)
2  107775            London     city     7556900  POINT (-0.12782 51.50725)
3  132591      Woolverstone   hamlet           0   POINT (1.18200 52.00276)
4  132593     Chelmondiston  village           0   POINT (1.20875 51.98990)

### Task 2: Examine Datasets

In [4]:
# display a map with the countries outlined. 

m = folium.Map([49.71566, 13.109678], tiles='CartoDB Positron', zoom_start=3)

folium.GeoJson(geojson_europe).add_to(m)

m

In [5]:
# Look at the head of the interest data.
interest.head()

osm_id              name     type  population                   geometry
0       2  Wiesbaden-Naurod  village           0   POINT (8.30130 50.13594)
1  104849           Bristol     city           0  POINT (-2.59539 51.45582)
2  107775            London     city     7556900  POINT (-0.12782 51.50725)
3  132591      Woolverstone   hamlet           0   POINT (1.18200 52.00276)
4  132593     Chelmondiston  village           0   POINT (1.20875 51.98990)

### Task 3: Choropleth
Now that the data is ready to be used let's create a Choropleth map using the European Countries dataset that includes the population numbers.  

In [6]:
## M7:P1:Cell03
# Add Your Code for creating a color map here, it is your choice on color scale used. Display the scale
# -----------------------------------------------------------------------------------------------------
from branca.colormap import linear

europe = europe.astype({'POP2005': int})

colormap = linear.OrRd_03.scale(
    europe.POP2005.min(),
    europe.POP2005.max())

print(colormap(5.))

colormap


#fee8c8ff


In [7]:
## M7:P1:Cell04
# Add Your Code for creating a population dictionary it should include name and the population. 
# --------------------------------------------------------------------------------------------
population_dict = europe.set_index('NAME')['POP2005']

population_dict['Azerbaijan']


8352021

In [8]:
## M7:P1:Cell05
# Add Your Code to create a folium map that is displaying the Choropleth. 
# -----------------------------------------------------------------------

# Create a map object centered to (47.751569, 1.675063), starting at zoom level 3 and CartoDB Positron map tiles. 
m = folium.Map([47.751569, 1.675063], tiles='CartoDB Positron', zoom_start=3)

#folium.GeoJson(geojson_europe).add_to(m)

#style function
def style_function(feature):
    return {
        'fillOpacity': 0.9,
        'weight': 1,
       # 'Use the line below to build your fillColor.
       # 'fillColor': colormap(population_dict[feature[/*This will not be id as the two datasets do not align on id*/]])
        'fillColor' : colormap(population_dict[feature['properties']['NAME']])
    }

# apply the county outlines to the map and save this object as Choropleth
Choropleth = folium.GeoJson(geojson_europe, #Data goes here, 
                            name='Choropleth', 
               style_function=lambda feature: {
                'fillColor': colormap(population_dict[feature['properties']['NAME']]),
                'color' : 'black',
                'weight' : 1,
                'fillOpacity' : .9,
               } 
                          
              )


# apply the county outlines to the map, XXXX needs to be replaced
folium.GeoJson(geojson_europe,
               name='Choropleth',
               style_function=style_function
              ).add_to(m)

# Overlay the image to the map


# display map
m

### Task 4: Markers
Now lets create a map and place the first 100 points of interest on it. 

In [10]:
interest['lon'] = interest['geometry'].x
interest['lat'] = interest['geometry'].y
interest['name'] = interest.name.astype(str)

interest.head()

osm_id              name     type  population                   geometry  \
0       2  Wiesbaden-Naurod  village           0   POINT (8.30130 50.13594)   
1  104849           Bristol     city           0  POINT (-2.59539 51.45582)   
2  107775            London     city     7556900  POINT (-0.12782 51.50725)   
3  132591      Woolverstone   hamlet           0   POINT (1.18200 52.00276)   
4  132593     Chelmondiston  village           0   POINT (1.20875 51.98990)   

        lon        lat  
0  8.301303  50.135944  
1 -2.595393  51.455817  
2 -0.127820  51.507252  
3  1.182003  52.002757  
4  1.208746  51.989904

In [11]:
help(MarkerCluster)

Help on class MarkerCluster in module folium.plugins.marker_cluster:

class MarkerCluster(folium.elements.JSCSSMixin, folium.map.Layer)
 |  MarkerCluster(locations=None, popups=None, icons=None, name=None, overlay=True, control=True, show=True, icon_create_function=None, options=None, **kwargs)
 |  
 |  Provides Beautiful Animated Marker Clustering functionality for maps.
 |  
 |  Parameters
 |  ----------
 |  locations: list of list or array of shape (n, 2).
 |      Data points of the form [[lat, lng]].
 |  popups: list of length n, default None
 |      Popup for each marker, either a Popup object or a string or None.
 |  icons: list of length n, default None
 |      Icon for each marker, either an Icon object or a string or None.
 |  name : string, default None
 |      The name of the Layer, as it will appear in LayerControls
 |  overlay : bool, default True
 |      Adds the layer as an optional overlay (True) or the base layer (False).
 |  control : bool, default True
 |      Whethe

In [12]:
## M7:P1:Cell06
# Add Your Code to create a folium map that is displaying the first 100 points of interest as cluster markers.
# When a user clicks on a single marker the marker should display the name of the point of interest. 
# ------------------------------------------------------------------------------------------------------------

# Create a map object centered to (47.751569, 1.675063), starting at zoom level 3 and Open Street map tiles. 
m1 = folium.Map([47.751569, 1.675063], tiles='OpenStreetMap', zoom_start=3)

# Create a loop to iterator over the points of interest use if index == 100: break to stop the loop at 100. 

labels, locations = [], []

for index, row in interest.iterrows():
    if index < 100:
        locations.append([row['lat'], row['lon']])
        labels.append('<i>' + row['name'] + '</i>')
    if index == 100:
        break

Cluster = MarkerCluster(locations=locations, popups=labels, name='Places of Interest')

# add the markers to the map
h = folium.FeatureGroup(name='points')    
h.add_child(MarkerCluster(locations=locations, popups=labels, name='Places of Interest'))

# Yes, I know popups not require but its added
# display map

m1.add_child(h)

### Task 5: One Map 
Now that you have created two different maps, let's make one map that has two layers instead. 
No code should need to be added. 

In [13]:
# create map
one_map = folium.Map([47.751569, 1.675063], tiles='Stamen Toner', zoom_start=6)

# Add Marker Cluster
one_map.add_child(Cluster)

# Add Choropleth
one_map.add_child(Choropleth)

# add the layer control
folium.LayerControl().add_to(one_map)

# display map
one_map

# Save your notebook, then `File > Close and Halt`